<a href="https://colab.research.google.com/github/satyashah/News-Prediction/blob/main/NewsPredictions.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import os
import csv
from sklearn import tree
import numpy as np


In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


# Set Up

In [ ]:
!pip install tensorflow==1.13.1

import tensorflow as tf 
import pandas as pd
import numpy as np 

from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.utils import shuffle

In [ ]:
!gsutil cp 'gs://cloudml-demo-lcm/SO_ml_tags_avocado_188k_v2.csv' ./

Copying gs://cloudml-demo-lcm/SO_ml_tags_avocado_188k_v2.csv...
/ [1 files][276.7 MiB/276.7 MiB]                                                
Operation completed over 1 objects/276.7 MiB.                                    


In [ ]:
data = pd.read_csv('SO_ml_tags_avocado_188k_v2.csv', names=['tags', 'original_tags', 'text'], header=0)
data = data.drop(columns=['original_tags'])
data = data.dropna()

data = shuffle(data, random_state=22)
data.head()

tags                                               text
182914  tensorflow,keras  avocado image captioning model not compiling b...
48361             pandas  return excel file from avocado with flask in f...
181447  tensorflow,keras  validating with generator (avocado) i'm trying...
66307             pandas  avocado multiindex dataframe selecting data gi...
11283             pandas  get rightmost non-zero value position for each...

In [ ]:
tags_split = [tags.split(',') for tags in data['tags'].values]
print(tags_split)

[['tensorflow', 'keras'], ['pandas'], ['tensorflow', 'keras'], ['pandas'], ['pandas'], ['pandas'], ['pandas'], ['tensorflow'], ['pandas'], ['matplotlib'], ['matplotlib'], ['tensorflow'], ['matplotlib'], ['scikitlearn'], ['scikitlearn'], ['scikitlearn'], ['pandas'], ['keras'], ['pandas'], ['matplotlib'], ['scikitlearn'], ['pandas'], ['pandas'], ['pandas'], ['keras'], ['pandas'], ['pandas'], ['pandas'], ['tensorflow'], ['tensorflow'], ['pandas'], ['tensorflow'], ['pandas'], ['pandas'], ['pandas'], ['tensorflow'], ['matplotlib'], ['matplotlib'], ['matplotlib'], ['pandas'], ['tensorflow'], ['keras'], ['pandas'], ['matplotlib'], ['pandas'], ['scikitlearn'], ['pandas'], ['pandas'], ['matplotlib', 'scikitlearn'], ['tensorflow', 'keras'], ['pandas', 'scikitlearn'], ['pandas'], ['tensorflow'], ['pandas', 'scikitlearn'], ['scikitlearn'], ['pandas'], ['pandas'], ['pandas'], ['pandas'], ['tensorflow'], ['tensorflow'], ['pandas'], ['scikitlearn'], ['scikitlearn'], ['tensorflow'], ['pandas'], ['tens

In [ ]:
tag_encoder = MultiLabelBinarizer()
tags_encoded = tag_encoder.fit_transform(tags_split)
num_tags = len(tags_encoded[0])
print(data['text'].values[0])
print(tag_encoder.classes_)
print(tags_encoded[0])

avocado image captioning model not compiling because of concatenate layer when mask_zero=true in a previous layer i am new to avocado and i am trying to implement a model for an image captioning project.   i am trying to reproduce the model from image captioning pre-inject architecture (the picture is taken from this paper: where to put the image in an image captioning generator) (but with a minor difference: generating a word at each time step instead of only generating a single word at the end), in which the inputs for the lstm at the first time step are the embedded cnn features. the lstm should support variable input length and in order to do this i padded all the sequences with zeros so that all of them have maxlen time steps.  the code for the model i have right now is the following:    def get_model(model_name, batch_size, maxlen, voc_size, embed_size,          cnn_feats_size, dropout_rate):      # create input layer for the cnn features     cnn_feats_input = input(shape=(cnn_fe

In [ ]:
train_size = int(len(data) * .8)
print ("Train size: %d" % train_size)
print ("Test size: %d" % (len(data) - train_size))

Train size: 150559
Test size: 37640


In [ ]:
train_tags = tags_encoded[:train_size]
test_tags = tags_encoded[train_size:]
print(train_tags,test_tags)

[[1 0 0 0 1]
 [0 0 1 0 0]
 [1 0 0 0 1]
 ...
 [0 0 1 0 0]
 [0 1 0 0 0]
 [0 0 0 0 1]] [[0 0 1 0 0]
 [0 0 1 0 0]
 [0 1 1 0 0]
 ...
 [0 0 1 0 0]
 [0 0 0 0 1]
 [0 1 0 0 0]]


In [ ]:
%%writefile preprocess.py

from tensorflow.keras.preprocessing import text

class TextPreprocessor(object):
  def __init__(self, vocab_size):
    self._vocab_size = vocab_size
    self.tokenizer = None
  
  def create_tokenizer(self, text_list):
    tokenizer = text.Tokenizer(num_words=self._vocab_size)
    tokenizer.fit_on_texts(text_list)
    self.tokenizer = tokenizer
    print(tokenizer)

  def transform_text(self, text_list):
    text_matrix = self.tokenizer.texts_to_matrix(text_list)
    return text_matrix

Overwriting preprocess.py


In [ ]:

from preprocess import TextPreprocessor

VOCAB_SIZE=400 # This is a hyperparameter, try out different values for your dataset

train_qs = data['text'].values[:train_size]
test_qs = data['text'].values[train_size:]

print(train_qs)

processor = TextPreprocessor(VOCAB_SIZE)
processor.create_tokenizer(train_qs)

body_train = processor.transform_text(train_qs)
body_test = processor.transform_text(test_qs)

['avocado image captioning model not compiling because of concatenate layer when mask_zero=true in a previous layer i am new to avocado and i am trying to implement a model for an image captioning project.   i am trying to reproduce the model from image captioning pre-inject architecture (the picture is taken from this paper: where to put the image in an image captioning generator) (but with a minor difference: generating a word at each time step instead of only generating a single word at the end), in which the inputs for the lstm at the first time step are the embedded cnn features. the lstm should support variable input length and in order to do this i padded all the sequences with zeros so that all of them have maxlen time steps.  the code for the model i have right now is the following:    def get_model(model_name, batch_size, maxlen, voc_size, embed_size,          cnn_feats_size, dropout_rate):      # create input layer for the cnn features     cnn_feats_input = input(shape=(cnn_

In [ ]:
print(len(body_train[0]))
print(body_train[0])

print(len(body_test[0]))
print(body_test[0])

400
[0. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 0. 0. 1. 1. 1. 0. 1. 1. 1. 0.
 0. 1. 1. 0. 1. 1. 1. 0. 1. 0. 1. 0. 0. 1. 0. 0. 0. 1. 0. 1. 0. 1. 1. 0.
 1. 0. 0. 1. 1. 1. 1. 1. 0. 1. 0. 1. 1. 1. 1. 0. 0. 0. 1. 1. 0. 0. 0. 0.
 1. 0. 1. 1. 0. 1. 0. 0. 1. 1. 1. 1. 1. 1. 0. 1. 1. 0. 1. 1. 1. 1. 0. 1.
 0. 0. 1. 1. 1. 0. 1. 0. 1. 1. 1. 1. 0. 1. 0. 0. 1. 0. 1. 1. 0. 1. 1. 1.
 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0.
 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 1. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0.
 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0.
 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1. 1. 0.
 0. 0. 0. 1. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0

# Decision Trees


In [ ]:
copied_path = 'gdrive/MyDrive/longNews.csv' #remove ‘content/’ from path then use 
data = pd.read_csv(copied_path, encoding='latin-1', names=["Index","date","year","month","day","author",'title',"article","url","section","publication","% Change"], header=0)
data.head()
print(len(data))

9707


In [ ]:
data = data.drop(columns=["Index","date","year","month","day"])
data.head()

author  ...  % Change
0   Lee Drutman  ...  0.006040
1   Scott Davis  ... -0.003429
2                ...  0.011578
3                ...  0.003546
4                ... -0.010883

[5 rows x 7 columns]

In [ ]:
marketChange = data["% Change"].values.tolist()
print(marketChange)

[0.006040422101898929, -0.003429446674527021, 0.011577829646784284, 0.003545973754446247, -0.010883238867769198, 0.0003802288467043704, -0.001224438775510186, -0.006717484059580537, 0.00029288747006421317, -0.0062974184931913505, -0.003071463367021765, -0.001224438775510186, 0.0037904417047833366, -0.002283000828341191, 0.002826101652465361, -0.007600229541726926, 0.00832511131027493, 0.015830769282399775, 0.00906599052224908, -0.016914495356521148, -0.001289986660902557, -0.0008447693522173397, 0.009015664348695315, -0.003777198466575185, 0.0015628790748737824, 0.004191848204613323, 0.002177417415756825, 0.016144349477682812, -0.00930053401690543, -0.00045277218093558026, -0.00024226390198902467, 0.002604305586088031, -0.005097812610519141, 0.01068086834779671, 0.0023120308154733252, 0.003545973754446247, 0.008754973464256334, -0.003464969919184572, -0.005596997611961104, 0.001864499642896202, 0.005717501264878374, 0.002257195668752356, -0.006776251242694315, -0.0013600751902664064, -

In [ ]:
train_size = int(len(data) * .8)
print ("Train size: %d" % train_size)
print ("Test size: %d" % (len(data) - train_size))

Train size: 7765
Test size: 1942


In [ ]:
train_marketChange = marketChange[:train_size]
test_marketChange = marketChange[train_size:]
print(train_marketChange,test_marketChange)

[0.006040422101898929, -0.003429446674527021, 0.011577829646784284, 0.003545973754446247, -0.010883238867769198, 0.0003802288467043704, -0.001224438775510186, -0.006717484059580537, 0.00029288747006421317, -0.0062974184931913505, -0.003071463367021765, -0.001224438775510186, 0.0037904417047833366, -0.002283000828341191, 0.002826101652465361, -0.007600229541726926, 0.00832511131027493, 0.015830769282399775, 0.00906599052224908, -0.016914495356521148, -0.001289986660902557, -0.0008447693522173397, 0.009015664348695315, -0.003777198466575185, 0.0015628790748737824, 0.004191848204613323, 0.002177417415756825, 0.016144349477682812, -0.00930053401690543, -0.00045277218093558026, -0.00024226390198902467, 0.002604305586088031, -0.005097812610519141, 0.01068086834779671, 0.0023120308154733252, 0.003545973754446247, 0.008754973464256334, -0.003464969919184572, -0.005596997611961104, 0.001864499642896202, 0.005717501264878374, 0.002257195668752356, -0.006776251242694315, -0.0013600751902664064, -

In [ ]:
#%%writefile preprocess.py

from tensorflow.keras.preprocessing import text

class TextPreprocessor():
  def __init__(self, vocab_size):
    self._vocab_size = vocab_size
    self._tokenizer = None
  
  def create_tokenizer(self, text_list):
    tokenizer = text.Tokenizer(num_words=self._vocab_size)
    tokenizer.fit_on_texts(text_list)
    self._tokenizer = tokenizer
  
  def getTokens(self):
    print(self._tokenizer.to_json(indent = 4))

  def transform_text(self, text_list):
    text_matrix = self._tokenizer.texts_to_matrix(text_list)
    return text_matrix

In [ ]:
#from preprocess import TextPreprocessor
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stopwrds = stopwords.words('english')
print(stopwrds)
VOCAB_SIZE=400 # This is a hyperparameter, try out different values for your dataset

train_qs = data['title'].values[:train_size]
test_qs = data['title'].values[train_size:]

# print(train_qs[0])
# for val in range(len(train_qs)):
#   for i in stopwrds:
#     train_qs[val] = train_qs[val].replace(" " + i + " ",' ')
# print(train_qs[0])

processor = TextPreprocessor(VOCAB_SIZE)
processor.create_tokenizer(train_qs)

processor.getTokens()

body_train = processor.transform_text(train_qs)
body_test = processor.transform_text(test_qs)

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'bo

In [ ]:
print(len(body_train[0]))
print(body_train[0])

400
[0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0

In [ ]:
X = body_train
Y = train_marketChange
print(X,Y)
clf = tree.DecisionTreeRegressor()
clf = clf.fit(X, Y)

[[0. 1. 0. ... 0. 0. 0.]
 [0. 1. 1. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 1. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]] [0.006040422101898929, -0.003429446674527021, 0.011577829646784284, 0.003545973754446247, -0.010883238867769198, 0.0003802288467043704, -0.001224438775510186, -0.006717484059580537, 0.00029288747006421317, -0.0062974184931913505, -0.003071463367021765, -0.001224438775510186, 0.0037904417047833366, -0.002283000828341191, 0.002826101652465361, -0.007600229541726926, 0.00832511131027493, 0.015830769282399775, 0.00906599052224908, -0.016914495356521148, -0.001289986660902557, -0.0008447693522173397, 0.009015664348695315, -0.003777198466575185, 0.0015628790748737824, 0.004191848204613323, 0.002177417415756825, 0.016144349477682812, -0.00930053401690543, -0.00045277218093558026, -0.00024226390198902467, 0.002604305586088031, -0.005097812610519141, 0.01068086834779671, 0.0023120308154733252, 0.003545973754446247, 0.008754973464256334, -0.0

In [ ]:
results = clf.predict(body_test)
print(results)

[-0.00102138  0.00029688  0.00981769 ...  0.00354597 -0.01088324
  0.00015517]


In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure


# data to plot
n_groups = len(results)
means_test = results
means_actual = test_marketChange

# create plot
fig, ax = plt.subplots()
figure(figsize=(18, 16), dpi=80)
index = np.arange(n_groups)
bar_width = 0.35
opacity = 0.8

rects1 = plt.bar(index, means_test, bar_width,
alpha=opacity,
color='b',
label='Test')

rects2 = plt.bar(index + bar_width, means_actual, bar_width,
alpha=opacity,
color='g',
label='Result')

# plt.xlabel('Person')
# plt.ylabel('Scores')
# plt.title('Scores by person')
# plt.xticks(index + bar_width, ('A', 'B', 'C', 'D'))
plt.legend()

plt.tight_layout()
figure(figsize=(18, 16), dpi=80)
plt.show()

In [ ]:
deviation= 0
for i in range(len(results)):
  deviation += abs(results[i]-test_marketChange[i])
avgDevation = deviation/len(results)
print("Deviation:",avgDevation)

In [ ]:
percentCorrect = 0
for i in range(len(results)):
  if results[i] > 0 and test_marketChange[i] > 0:
    percentCorrect += 1

percentCorrect = percentCorrect/len(results)
print(percentCorrect*100,"%")

31.513903192584962 %


In [ ]:
money = 1000
bestCase = 1000
norm = 1000
for i in range(len(means_test)):
  if results[i]>0:
    money = money + money*test_marketChange[i]
  if test_marketChange[i]>0:
    bestCase = bestCase + bestCase*test_marketChange[i]
  norm = norm + norm * test_marketChange[i]
print("Your Run:", money,"\nBest Run:", bestCase, "\nNormal:", norm)

Your Run: 2172.3283489581377 
Best Run: 350947.3376247138 
Normal: 3821.050935456816


#Neural Network

In [ ]:
copied_path = 'gdrive/MyDrive/longNews.csv' #remove ‘content/’ from path then use 
data = pd.read_csv(copied_path, encoding='latin-1', names=["Index","date","year","month","day","author",'title',"article","url","section","publication","% Change"], header=0)
data.head()
print(len(data))

9707


In [ ]:
data = data.drop(columns=["Index","date","year","month","day"])
data.head()

author  ...  % Change
0   Lee Drutman  ...  0.006040
1   Scott Davis  ... -0.003429
2                ...  0.011578
3                ...  0.003546
4                ... -0.010883

[5 rows x 7 columns]

In [ ]:
marketChange = data["% Change"].values.tolist()
print(marketChange)

[0.006040422101898929, -0.003429446674527021, 0.011577829646784284, 0.003545973754446247, -0.010883238867769198, 0.0003802288467043704, -0.001224438775510186, -0.006717484059580537, 0.00029288747006421317, -0.0062974184931913505, -0.003071463367021765, -0.001224438775510186, 0.0037904417047833366, -0.002283000828341191, 0.002826101652465361, -0.007600229541726926, 0.00832511131027493, 0.015830769282399775, 0.00906599052224908, -0.016914495356521148, -0.001289986660902557, -0.0008447693522173397, 0.009015664348695315, -0.003777198466575185, 0.0015628790748737824, 0.004191848204613323, 0.002177417415756825, 0.016144349477682812, -0.00930053401690543, -0.00045277218093558026, -0.00024226390198902467, 0.002604305586088031, -0.005097812610519141, 0.01068086834779671, 0.0023120308154733252, 0.003545973754446247, 0.008754973464256334, -0.003464969919184572, -0.005596997611961104, 0.001864499642896202, 0.005717501264878374, 0.002257195668752356, -0.006776251242694315, -0.0013600751902664064, -

In [ ]:
train_size = int(len(data) * .8)
print ("Train size: %d" % train_size)
print ("Test size: %d" % (len(data) - train_size))

Train size: 7765
Test size: 1942


In [ ]:
train_marketChange = marketChange[:train_size]
test_marketChange = marketChange[train_size:]
print(train_marketChange,test_marketChange)

[0.006040422101898929, -0.003429446674527021, 0.011577829646784284, 0.003545973754446247, -0.010883238867769198, 0.0003802288467043704, -0.001224438775510186, -0.006717484059580537, 0.00029288747006421317, -0.0062974184931913505, -0.003071463367021765, -0.001224438775510186, 0.0037904417047833366, -0.002283000828341191, 0.002826101652465361, -0.007600229541726926, 0.00832511131027493, 0.015830769282399775, 0.00906599052224908, -0.016914495356521148, -0.001289986660902557, -0.0008447693522173397, 0.009015664348695315, -0.003777198466575185, 0.0015628790748737824, 0.004191848204613323, 0.002177417415756825, 0.016144349477682812, -0.00930053401690543, -0.00045277218093558026, -0.00024226390198902467, 0.002604305586088031, -0.005097812610519141, 0.01068086834779671, 0.0023120308154733252, 0.003545973754446247, 0.008754973464256334, -0.003464969919184572, -0.005596997611961104, 0.001864499642896202, 0.005717501264878374, 0.002257195668752356, -0.006776251242694315, -0.0013600751902664064, -

In [ ]:
#%%writefile preprocess.py

from tensorflow.keras.preprocessing import text

class TextPreprocessor():
  def __init__(self, vocab_size):
    self._vocab_size = vocab_size
    self._tokenizer = None
  
  def create_tokenizer(self, text_list):
    tokenizer = text.Tokenizer(num_words=self._vocab_size)
    tokenizer.fit_on_texts(text_list)
    self._tokenizer = tokenizer
  
  def getTokens(self):
    print(self._tokenizer.to_json(indent = 4))

  def transform_text(self, text_list):
    text_matrix = self._tokenizer.texts_to_matrix(text_list)
    return text_matrix

In [ ]:
#from preprocess import TextPreprocessor
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stopwrds = stopwords.words('english')
print(stopwrds)
VOCAB_SIZE=400 # This is a hyperparameter, try out different values for your dataset

train_qs = data['title'].values[:train_size]
test_qs = data['title'].values[train_size:]

# print(train_qs[0])
# for val in range(len(train_qs)):
#   for i in stopwrds:
#     train_qs[val] = train_qs[val].replace(" " + i + " ",' ')
# print(train_qs[0])

processor = TextPreprocessor(VOCAB_SIZE)
processor.create_tokenizer(train_qs)

processor.getTokens()

body_train = processor.transform_text(train_qs)
body_test = processor.transform_text(test_qs)

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'bo

In [ ]:
from sklearn.neural_network import MLPRegressor

X = body_train
y = np.asarray(train_marketChange, dtype="float")
print(y)

clf = MLPRegressor(random_state=1, max_iter=500)
clf.fit(X,y)

[ 0.00604042 -0.00342945  0.01157783 ...  0.00318417 -0.00221932
  0.00070511]


MLPRegressor(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
             beta_2=0.999, early_stopping=False, epsilon=1e-08,
             hidden_layer_sizes=(100,), learning_rate='constant',
             learning_rate_init=0.001, max_fun=15000, max_iter=500,
             momentum=0.9, n_iter_no_change=10, nesterovs_momentum=True,
             power_t=0.5, random_state=1, shuffle=True, solver='adam',
             tol=0.0001, validation_fraction=0.1, verbose=False,
             warm_start=False)

In [ ]:
clf.score(X,y)

-0.1563295049097435

In [ ]:
results = clf.predict(body_test)
print(results)
print(test_marketChange)

[ 0.03265932  0.00853123 -0.01725789 ...  0.02850773  0.09882555
  0.01017263]
[-0.0062974184931913505, 0.0018593357158729288, 0.0013335791488556616, -0.00036648342922746425, 0.013022546477004905, 0.008461434648215542, -0.003186878612847431, 0.0035777960312136665, -0.0012550866219939063, 0.011612256941903472, -0.013475289443698723, -0.004048383955907033, -0.0031909291499997447, -0.000997417079467007, 0.0013612308504031725, 0.004640668097044071, 0.001073867245987817, 0.00046750980766055526, 0.009992986441275768, -0.0029330990130174302, -0.012614193421661769, 0.008754973464256334, 0.005583459013432507, 0.006016056380148266, -0.017909854902827763, 0.005442568473123575, 0.003153080958557999, 0.0004851811281082033, 0.010698444391126148, 0.0024810463986207304, 0.0005314300819036846, 0.0024810463986207304, 0.0011448623788116571, 0.009312782877898544, 0.012111780726373476, -0.0006885884593457912, 4.597478963153778e-05, 0.005426169978933814, 0.0013311325417297538, 0.0018970292018089907, 0.01161

In [ ]:
percentCorrect = 0
for i in range(len(results)):
  if results[i] > 0 and test_marketChange[i] > 0:
    percentCorrect += 1

percentCorrect = percentCorrect/len(results)
print(percentCorrect*100,"%")

27.29145211122554 %
